In [1]:
import pandas as pd
import numpy as np
import nltk  
from sklearn.feature_extraction.text import CountVectorizer, TfidfVectorizer

In [2]:
data = pd.read_csv("hillary-clinton-emails/Emails.csv")
data_rawtext = data[u'RawText']

# Наиболее частые биграммы и коллокации

Обработка текста для первых экспериментов: 
- сырые тексты из'RawText', так как 'ExtractedBodyText' не содержит текстов вложенных документов;
- стандартный analyzer='word'

In [34]:
vectorizer = CountVectorizer(analyzer='word', ngram_range=(2, 2))
analyser = vectorizer.build_analyzer()
bigrams_counts = dict()

def counter(text):
    bigrams = analyser(text)
    bigrams_vocabulary = set(bigrams)
    for bigram in bigrams_vocabulary:
        if bigram not in bigrams_counts:
            bigrams_counts[bigram] = bigrams.count(bigram)
        else:
            bigrams_counts[bigram] += bigrams.count(bigram)

x = map(counter, data_rawtext)

In [23]:
# топ биграмм для всего корпуса
sorted_bigrams = sorted(bigrams_counts.items(), key=lambda x: x[1], reverse=True)
for item in sorted_bigrams[:20]:
    print item

(u'of state', 28179)
(u'department of', 27170)
(u'doc no', 26534)
(u'case no', 26527)
(u'state case', 26518)
(u'unclassified department', 26507)
(u'20439 doc', 24833)
(u'2014 20439', 24808)
(u'no 2014', 24785)
(u'31 2015', 18644)
(u'08 31', 14255)
(u'date 08', 14238)
(u'of the', 14036)
(u'state gov', 11055)
(u'in the', 10178)
(u'release in', 7916)
(u'2015 release', 7466)
(u'message from', 7266)
(u'original message', 7233)
(u'subject re', 6734)


In [17]:
import nltk
from nltk.collocations import *

In [15]:
vectorizer_1 = CountVectorizer(analyzer='word', ngram_range=(1, 1))
analyser_1 = vectorizer_1.build_analyzer()
bigram_measures = nltk.collocations.BigramAssocMeasures()

In [12]:
#топ коллокаций для всего корпуса с использованием analyzer='word'

finder = BigramCollocationFinder.from_words(analyser_1("\n".join(data_rawtext)))
for bi in finder.nbest(bigram_measures.pmi, 20):
    print bi[0], bi[1]

0000779fd2ac htmly
00144fea 49p
0027 ulannbaniar
0081 907203
0111111111111115 4111111111111111111111111
01142104a39 1ar
011anta humala
0140 matioalgo
01702 ce9k4
01_attorney_general_andrew_cuomo_subpoenas_contracts_won_by_clients_of firm_tied_to
01a 02793
01cb267a b4a44080
0203tatg ownecopetroleos
020department 020of
020estimate 20child
020of modn
026c 023821
02793 fatl
02fregion 2f271
03d3320400 26crt


In [33]:
#тоже самое, но с ограничением снизу на частоту биграмы

finder = BigramCollocationFinder.from_words(analyser_1("\n".join(data_rawtext)))
finder.apply_freq_filter(100)
for bi in finder.nbest(bigram_measures.pmi, 20):
    print bi[0], bi[1]

scanlon amy
jacobs janice
sri lanka
curtis meghann
sinn fein
bin laden
balderston kris
rodriguez miguel
macmanus joseph
strobe talbott
das gis
oscar flores
gis dos
harold hongju
hanley monica
port au
21st century
op ed
au prince
koh harold


# Простейшая кластеризация

In [3]:
# признаки - биграммы, встречающиеся не менее, чем в 4 письмах, но не более, чем в 40% половине ото всех писем
vectorizer = TfidfVectorizer(analyzer='word', ngram_range=(2, 2),  min_df=0.0005, max_df=0.4)
matrix = vectorizer.fit_transform(data_rawtext)

In [4]:
print(matrix.shape)
print vectorizer.stop_words_

(7945, 102905)
set([u'james rice', u'personal effects', u'smuggling kidnapping', u'cognitive advantage', u'clergy they', u'pornography on', u'saying go', u'palin 48', u'it serious', u'philosophical bearings', u'published mr', u'palin 42', u'c05770144 date', u'palin 40', u'allow this', u'then peace', u'walking distance', u'147616 and', u'icbm new', u'changes if', u'intellectuals and', u'it absolutely', u'rousing ovation', u'why using', u'were tern', u'death videos', u'ok am', u'changes it', u'ok as', u'ok at', u'be constructed', u'bode well', u'heffern keith', u'and burdened', u'nays and', u'monday mrs', u'comments ftij', u'hurricanes as', u'switch between', u'populists and', u'house sent', u'all attached', u'c05765765 date', u'intimates chief', u'tigers and', u'of ngos', u'corporate tax', u'work these', u'to acorn', u'gratifying now', u'gc ssc1', u'book makes', u'had envisioned', u'forest hills', u'month hillsborough', u'std you', u'lastly championship', u'the rebalancing', u'down tues

In [4]:
from sklearn.cluster import KMeans
number_clusters=15
model = KMeans(n_clusters=number_clusters, n_jobs=-1, max_iter=150)
preds = model.fit_predict(matrix)

In [8]:
preds[:-50]

array([12, 12, 12, ..., 11,  1, 10], dtype=int32)

# Визуализация

Визуализируем с помощью часто встречающихся в кластере коллокаций, отсутсвующих в других кластерах.

In [10]:
# выделим темы писем, где возможно
# ищем заголовок
subject_keywords = [ 'subject:', 'fw:', 're:']
count = 0
subjects = []
for text in data_rawtext:
    found = False
    for line in text.split('\n'):
        if len(line.split())>0: 
            if line.split()[0].lower() in subject_keywords:
                for keyword in subject_keywords:
                    line = line.lower().replace(keyword, "")
                subjects.append(line.strip())
                found = True
                break
    if not found:
        subjects.append("")
        count += 1
        
print len(subjects)   
print count #письма без заголовка

7945
759


In [13]:
# для сугубо личного удобства складывем кластера в словарик
numbers = dict()
texts = dict()
sub = dict()
for i in range(number_clusters):
    numbers[i] = 0
    texts[i] = []
    sub[i] = []
    for j, p in enumerate(preds):
        if i == p:
            numbers[i]+=1 
            texts[i].append(data_rawtext[j])
            sub[i].append(subjects[j])
print "Размеры кластеров:\n", numbers

Размеры кластеров:
{0: 354, 1: 595, 2: 71, 3: 1110, 4: 806, 5: 241, 6: 100, 7: 154, 8: 1133, 9: 270, 10: 182, 11: 1668, 12: 295, 13: 499, 14: 467}


Кластеры получились сравнимого размера. Наверное, это неплохо :)

In [20]:
#Давайте визуализируем кластеры по часто встречающихся в них коллакациях

vectorizer_cl = CountVectorizer(analyzer='word', ngram_range=(1, 1))
analyser_cl = vectorizer_cl.build_analyzer()
bigram_measures = nltk.collocations.BigramAssocMeasures()
for i in range(number_clusters):
    finder = BigramCollocationFinder.from_words(analyser_1("\n".join(texts[i])))
    finder.apply_freq_filter(len(texts[i]) * 0.05)
    print "Кластер ",  i, "\n"
    for bi in finder.nbest(bigram_measures.pmi, 10):
        print bi[0], bi[1]
    print "\n-------------\n"

Кластер  0 

hillsborough castle
moore anna
withers anne
casteel ezra
martin mcguinness
simmons krista
castle outside
hdr22 clintonemail
sullivan jacob
clintonemail com

-------------

Кластер  1 

dollars buy
buy little
little goodwill
holbrooke richard
mchale judith
aid dollars
aid workers
ni talks
cheryl millscd
talks sid

-------------

Кластер  2 

articulo168592 tres
asesores de
asp idnews
aspx id
association crimes
children refuge
chuzadas ilegales
following basic
id 58754
idnews 49968

-------------

Кластер  3 

sinn fein
jacobs janice
reines philippe
lib dems
mchale judith
slaughter anne
toiv nora
202 647
port au
au prince

-------------

Кластер  4 

feltman jeffrey
rodriguez miguel
united states
klevorick caitlin
burns william
reines philippe
human rights
steinberg james
http www
valmoro lona

-------------

Кластер  5 

didn miss
other windows
russo robert
personal acct
martin indyk
tom donilon
longer available
sure didn
amb holbrooke
fmr dep

-------------

Кластер  6 

e

**Комментарий**: в целом, выглядит разумно - в 11 кластере собрались словосочетания про права человека (human rights): Verma Richard - посол доброй воли, verveer melanne - борец за права человека
Кластер 10 - про восток, Далай Лама, Индия,  Пакестан, 
 Кластер 7 - про какие-то "бытовые" вопросы и переписки
 
 Хотя есть подозрение, что в эти списки попали адресаты и отправители писем

In [31]:
#Проверим гипотезу на кластере 13
print texts[13][15]
print texts[13][45]
print texts[13][90]

UNCLASSIFIED U.S. Department of State Case No. F-2014-20439 Doc No. C05758868 Date: 06/30/2015
RELEASE IN FULL
From: H <hrod17@clintonemail.com>
Sent: Thursday, July 2, 2009 6:06 PM
To: 'abedinh@state.gov'
Subject: Re: King Abdullah names Prince Hussein Crown Prince
What's Hussein like?
Original Message
From: Abedin, Huma <AbedinH@state.gov>
To: H
Sent: Thu Jul 02 18:00:51 2009
Subject: Re: King Abdullah names Prince Hussein Crown Prince
Isn't a surprise since 5 years ago he removed his brother as official crown prince.
Basically he's not honoring his fathers dying wish but since constitution says it should be son (with brother as option) he
has clear authority to do it. I personally think this shows confidence in his position as he's not worried about an outcry
from his fathers loyalists.
Original Message
From: H <HDR22@clintonemail.com>
To: Abedin, Huma
Sent: Thu Jul 02 16:41:23 2009
Subject: Re: King Abdullah names Prince Hussein Crown Prince
What does this mean?
Original Message
Fr

# Про ассесоров 

1) 1 этап: с помощью сформируем топ 100 интерпретируемых биграмм/коллакации с максимальной степенью интерпретируемости из полученных при визуалиазации класетров.
2) 2 этап: для каждого письма проставить 1-3 биграммы из сформированного топ-100, либо указать, что ни одна не походит
